In [7]:
import pandas as pd

In [101]:
def get_genius_song_url(artist_name, song_name):
    song_name = song_name.replace(',', '').replace('\'', '').replace('.', '').replace('(', '').replace(')', '').replace('!','').replace('&','').replace('+', '').replace('?', '')
    base_url = "https://genius.com/"
    suffix = 'lyrics'
    artist_part = '-'.join(artist_name.split(' '))
    song_part = '-'.join(song_name.split(' '))
    return base_url + artist_part + '-' + song_part + '-' + suffix

In [102]:
def remove_bracketed_measures(tmp):
    start_find = ["[Intro","[Chorus", "[Verse", "[Pre-Chorus", "[Bridge"]
    for s in start_find:
        while (tmp.find(s) != -1):
            firstDelPos= tmp.find(s) # get the position of [
#             chorusDelPos = tmp.find("[Chorus")
#             firstDelPos = verseDelPos if chorusDelPos==-1 else chorusDelPos if verseDelPos==-1 else verseDelPos if verseDelPos < chorusDelPos else chorusDelPos
            secondDelPos=tmp[firstDelPos:].find("]") + firstDelPos # get the position of ]
            tmp = tmp.replace(tmp[firstDelPos:secondDelPos+1], "") # replace the string between two delimiters
    return tmp

def remove_nonalphanumeric(word):
    return " ".join([re.sub('[\W_]+', '', w) for w in word.split(' ')])

In [103]:
import urllib.request
import urllib.parse
import urllib.error
from bs4 import BeautifulSoup
import ssl
import json
import ast
import os
from urllib.request import Request, urlopen
from tqdm import tqdm

def get_genius_song_url(artist_name, song_name):
    song_name = song_name.replace(',', '').replace('\'', '').replace('.', '').replace('(', '').replace(')', '').replace('!','').replace('&','').replace('+', '').replace('?', '')
    base_url = "https://genius.com/"
    suffix = 'lyrics'
    artist_part = '-'.join(artist_name.split(' '))
    song_part = '-'.join(song_name.split(' '))
    return base_url + artist_part + '-' + song_part + '-' + suffix

def get_song_lyrics_from_genius(artist, song):
    ctx = ssl.create_default_context()
    ctx.check_hostname = False
    ctx.verify_mode = ssl.CERT_NONE

    # Input from user
    url = get_genius_song_url(artist, song)

    # Making the website believe that you are accessing it using a mozilla browser
    req = Request(url, headers = { 'User-Agent' : 'Mozilla/5.0' })
    webpage = urlopen(req).read()

    # Creating a BeautifulSoup object of the html page for easy extraction of data.

    soup = BeautifulSoup(webpage, 'html.parser')
    html = soup.prettify('utf-8')
    song_json = {}
    song_json["Lyrics"] = [];
    song_json["Comments"] = [];

    #Extract Title of the song
    for title in soup.findAll('title'):
        song_json["Title"] = title.text.strip()

    # Extract the release date of the song
    for span in soup.findAll('span', attrs = {'class': 'metadata_unit-info metadata_unit-info--text_only'}):
        song_json["Release date"] = span.text.strip()

    # Extract the Comments on the song
    for div in soup.findAll('div', attrs = {'class': 'rich_text_formatting'}):
        comments = div.text.strip().split("\n")
        for comment in comments:
            if comment!="":
                song_json["Comments"].append(comment);

    #Extract the Lyrics of the song
    for div in soup.findAll('div', attrs = {'class': 'lyrics'}):
        song_json["Lyrics"].append(div.text.strip().split("\n"));
    
    song_json['artist_name'] = artist
    song_json['song_name'] = song
    #Save the json created with the file name as title + .json
    with open("music_lyrics/" + song_json["Title"] + '.json', 'w+') as outfile:
        json.dump(song_json, outfile, indent = 4, ensure_ascii = False)

    # Save the html content into an html file with name as title + .html
    with open("music_lyrics/" + song_json["Title"] + '.html', 'wb') as file:
        file.write(html)

    return (' ').join(song_json['Lyrics'][0])


def build_song_lyrics_data(artists, songs):
    # For ignoring SSL certificate errors
    songs_dataset = pd.DataFrame()
    count = 0
    for i in tqdm(range(len(songs))):
        print("Artist: {}; Song: {}".format(artists[i], songs[i]))
        try:
            curr_lyrics = get_song_lyrics_from_genius(artists[i], songs[i])
            count = count + 1
            songs_dataset = songs_dataset.append(pd.DataFrame({'aritst': [artists[i]],
                                                               'song': [songs[i]], 
                                                               'lyrics': [curr_lyrics]}))
            if count % 100 == 0: 
                song_dataset.to_csv("song_lyrics_data_p7.csv", index=False)
        except Exception:
            print("Failed in Error")
        
    return songs_dataset

In [104]:
#!/usr/bin/python
#- * -coding: utf - 8 - * -

import urllib.request
import urllib.parse
import urllib.error
from bs4 import BeautifulSoup
import ssl
import json
import ast
import os
from urllib.request import Request, urlopen
from tqdm import tqdm

def build_song_lyrics_data(artists, songs):
    # For ignoring SSL certificate errors
    songs_dataset = pd.DataFrame()
    count = 0
    for i in tqdm(range(len(songs))):
        print("Artist: {}; Song: {}".format(artists[i], songs[i]))
        try:
            curr_lyrics = get_song_lyrics_from_genius(artists[i], songs[i])
            count = count + 1
            songs_dataset = songs_dataset.append(pd.DataFrame({'aritst': [artists[i]],
                                                               'song': [songs[i]], 
                                                               'lyrics': [curr_lyrics]}))
            if count % 100 == 0: 
                song_dataset.to_csv("song_lyrics_data_p7.csv", index=False)
        except Exception:
            print("Failed in Error")
        
    return songs_dataset

In [78]:
song_metadata = pd.read_csv("subsampled_genius_artist_spotify_song_metadata.csv")
genres = pd.read_csv("selected_artists.csv")
audio_features = pd.read_csv("subsampled_audio_features_p3.csv")

In [79]:
audio_data = song_metadata.merge(audio_features, left_on='song_uri', right_on='uri')

In [97]:
finished_idx = 2210+3000+3940+6190+2080

In [98]:
song_lyrics_data = build_song_lyrics_data(audio_data[finished_idx:].artist_name.values, audio_data[finished_idx:].song_name.values)










  0%|          | 0/13388 [00:00<?, ?it/s]

Artist: ScHoolboy Q; Song: Gangsta











  0%|          | 1/13388 [00:02<9:31:17,  2.56s/it]

Artist: ScHoolboy Q; Song: The Purge











  0%|          | 2/13388 [00:12<17:44:19,  4.77s/it]

...

Failed in Error
Artist: The Veronicas; Song: All I Have - Live











100%|█████████▉| 13387/13388 [6:41:09<00:01,  1.00s/it]

Failed in Error
Artist: The Veronicas; Song: Untouched - Live











100%|██████████| 13388/13388 [6:41:11<00:00,  1.80s/it]

Failed in Error


In [99]:
song_lyrics_data.to_csv("song_lyrics_audio_data_p7.csv",index=False)

In [100]:
song_lyrics_data

aritst                              song  \
0     ScHoolboy Q                           Gangsta   
0     ScHoolboy Q                         The Purge   
0     ScHoolboy Q                    Collard Greens   
0     ScHoolboy Q                    My Hatin Joint   
0     ScHoolboy Q  Gangsta in Designer (No Concept)   
..            ...                               ...   
0   The Veronicas                Someone Wake Me Up   
0   The Veronicas  Did You Miss Me (I'm a Veronica)   
0   The Veronicas                       You Ruin Me   
0   The Veronicas               If You Love Someone   
0   The Veronicas                        Let Me Out   

                                               lyrics  
0   [Produced by Nez & Rio]  [Intro: Joy] Hello......  
0   [Intro: Joy] My daddy said "Yeah, nigga"  [Hoo...  
0   [Intro: ScHoolboy Q] Yeah, yeah, yeah Oh, oh Y...  
0   [Produced by Mike WiLL Made-It]  [Intro] Nigga...  
0   [Intro] Nigga ain't got no concept to this shi...  
..                                                ...  
0   [Verse 1] We got the same friends We're gonna ...  
0   [Intro] I'm a Veronica  [Verse 1] Back with a ...  
0   [Verse 1 - Lisa] Job well done Standing ovatio...  
0   [Intro] If you love someone If you love someon...  
0   [Verse 1] I can't take the blame I can't take ...  

[8188 rows x 3 columns]

In [105]:
tmp = build_song_lyrics_data(['Alt-j'], ['Left Hand Free'])










  0%|          | 0/1 [00:00<?, ?it/s]

Artist: Alt-j; Song: Left Hand Free











100%|██████████| 1/1 [00:02<00:00,  2.37s/it]


In [107]:
tmp.to_csv("left_hand_free_lyrics.csv")